In [1]:
import time
import requests
from bs4 import BeautifulSoup
from tqdm.notebook import tqdm
from datetime import datetime, timedelta
from concurrent.futures import ThreadPoolExecutor, as_completed
import re

In [2]:
def generate_dates_m_d_Y_compatible(start_date, end_date):
    start = datetime.strptime(start_date, "%m/%d/%Y")
    end = datetime.strptime(end_date, "%m/%d/%Y")
    step = timedelta(days=1)
    
    date_list = []
    while start <= end:
        date_str = f"{start.month}/{start.day}/{start.year}"
        date_list.append(date_str)
        start += step
    
    return date_list


def get_search_results(url, retries=5, sleep_time=5):
    headers = {
        'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/121.0.0.0 Safari/537.36',
     }
    
    for attempt in range(retries):
        response = requests.get(url, headers=headers)
        
        if response.status_code == 200:
            print(response)
            soup = BeautifulSoup(response.text, 'html.parser')
            search_results = soup.find_all('a')
            
            links = [link['href'] for link in search_results if link.has_attr('href')]
            links = [x for x in links if 'https://www.bbc.com/news/' in x]
            links = [x for x in links if '/live/' not in x]
            links = [x.replace('/url?q=', '') for x in links]
            links = [x.split('&')[0] for x in links]
            links = [x for x in links if x[-1].isdigit()]
            
            return links
        else:
            print(f'Response status code {response.status_code}. Retrying in {sleep_time} seconds...')
            time.sleep(sleep_time)
    
    print("Failed to retrieve data after multiple attempts.")
    return []

In [11]:
url = 'https://www.google.com/search?q=news+site:bbc.com/news&tbs=cdr:1,cd_min:<DATE>,cd_max:<DATE>&tbm=nws&start=<START>'
max_page_num = 100
sleep_time = 1.0

start_date = "1/25/2024"
end_date = "2/3/2024"
dates = generate_dates_m_d_Y_compatible(start_date, end_date)

url_list = []
for date in dates:
    for start in [str(x * 10) for x in range(max_page_num)]:
        request_url = url.replace('<START>', start).replace('<DATE>', date)
        search_links = get_search_results(request_url)
        url_list += search_links
        print('-' * 100)
        print(f'date:{date} start:{start} total:{len(set(url_list))}')
        for link in search_links:
            print(link)
        if len(search_links) == 0:
            break
        time.sleep(sleep_time)

<Response [200]>
----------------------------------------------------------------------------------------------------
date:1/25/2024 start:0 total:10
https://www.bbc.com/news/science-environment-68071695
https://www.bbc.com/news/world-europe-68055420
https://www.bbc.com/news/av/world-asia-68093831
https://www.bbc.com/news/uk-england-sussex-68084883
https://www.bbc.com/news/business-68096633
https://www.bbc.com/news/world-europe-68099669
https://www.bbc.com/news/world-africa-68090485
https://www.bbc.com/news/world-68091321
https://www.bbc.com/news/world-68097190
https://www.bbc.com/news/entertainment-arts-67986987
<Response [200]>
----------------------------------------------------------------------------------------------------
date:1/25/2024 start:10 total:19
https://www.bbc.com/news/entertainment-arts-68092121
https://www.bbc.com/news/uk-68097048
https://www.bbc.com/news/business-68096905
https://www.bbc.com/news/world-europe-68095693
https://www.bbc.com/news/world-asia-india-680918

<Response [200]>
----------------------------------------------------------------------------------------------------
date:1/25/2024 start:150 total:122
https://www.bbc.com/news/uk-england-essex-68099217
https://www.bbc.com/news/uk-england-devon-68093443
https://www.bbc.com/news/uk-england-south-yorkshire-68072385
https://www.bbc.com/news/uk-northern-ireland-68096928
https://www.bbc.com/news/uk-england-devon-68098091
https://www.bbc.com/news/uk-england-leeds-68095107
https://www.bbc.com/news/uk-wales-68091801
https://www.bbc.com/news/uk-england-birmingham-68083458
https://www.bbc.com/news/av/uk-england-oxfordshire-68086177
<Response [200]>
----------------------------------------------------------------------------------------------------
date:1/25/2024 start:160 total:130
https://www.bbc.com/news/uk-england-lincolnshire-68096344
https://www.bbc.com/news/uk-england-sussex-68093639
https://www.bbc.com/news/uk-england-york-north-yorkshire-68088577
https://www.bbc.com/news/uk-england-stok

<Response [200]>
----------------------------------------------------------------------------------------------------
date:1/26/2024 start:30 total:233
https://www.bbc.com/news/uk-england-hampshire-68110405
https://www.bbc.com/news/uk-68102485
https://www.bbc.com/news/uk-northern-ireland-68103946
https://www.bbc.com/news/uk-68084538
https://www.bbc.com/news/uk-england-humber-68088978
https://www.bbc.com/news/uk-england-humber-68107920
https://www.bbc.com/news/uk-68107990
https://www.bbc.com/news/world-europe-guernsey-68109244
https://www.bbc.com/news/av/uk-england-london-68106831
<Response [200]>
----------------------------------------------------------------------------------------------------
date:1/26/2024 start:40 total:238
https://www.bbc.com/news/uk-england-merseyside-68112771
https://www.bbc.com/news/uk-47213842
https://www.bbc.com/news/world-europe-isle-of-man-68111411
https://www.bbc.com/news/uk-england-devon-68105900
https://www.bbc.com/news/uk-england-essex-68092898
<Respon

<Response [200]>
----------------------------------------------------------------------------------------------------
date:1/26/2024 start:180 total:351
https://www.bbc.com/news/uk-england-humber-68103464
https://www.bbc.com/news/uk-wales-68109597
https://www.bbc.com/news/uk-england-northamptonshire-68107007
https://www.bbc.com/news/uk-england-cambridgeshire-68106376
https://www.bbc.com/news/uk-england-somerset-68101761
https://www.bbc.com/news/uk-england-leicestershire-68108430
https://www.bbc.com/news/av/uk-england-birmingham-68108634
https://www.bbc.com/news/uk-politics-67892958
https://www.bbc.com/news/uk-england-leicestershire-68105827
https://www.bbc.com/news/uk-northern-ireland-68103938
<Response [200]>
----------------------------------------------------------------------------------------------------
date:1/26/2024 start:190 total:359
https://www.bbc.com/news/uk-england-sussex-68107196
https://www.bbc.com/news/uk-england-south-yorkshire-68106357
https://www.bbc.com/news/uk-eng

<Response [200]>
----------------------------------------------------------------------------------------------------
date:1/27/2024 start:30 total:460
https://www.bbc.com/news/uk-england-suffolk-68095926
https://www.bbc.com/news/uk-england-somerset-68069603
https://www.bbc.com/news/uk-wales-68096720
https://www.bbc.com/news/uk-england-sussex-68098105
https://www.bbc.com/news/av/uk-england-hampshire-68117575
https://www.bbc.com/news/uk-england-york-north-yorkshire-68107143
https://www.bbc.com/news/business-68078724
<Response [200]>
----------------------------------------------------------------------------------------------------
date:1/27/2024 start:40 total:470
https://www.bbc.com/news/uk-england-derbyshire-68068576
https://www.bbc.com/news/uk-england-cornwall-68006877
https://www.bbc.com/news/entertainment-arts-68088493
https://www.bbc.com/news/uk-scotland-68117194
https://www.bbc.com/news/uk-england-devon-68117088
https://www.bbc.com/news/uk-england-bristol-68107736
https://www.bb

...

<Response [200]>
----------------------------------------------------------------------------------------------------
date:1/31/2024 start:170 total:1357
https://www.bbc.com/news/uk-politics-68154294
https://www.bbc.com/news/technology-68140296
https://www.bbc.com/news/uk-england-bristol-68152005
https://www.bbc.com/news/business-68130784
https://www.bbc.com/news/uk-wales-politics-68152933
<Response [200]>
----------------------------------------------------------------------------------------------------
date:1/31/2024 start:180 total:1367
https://www.bbc.com/news/uk-england-kent-68154285
https://www.bbc.com/news/av/uk-politics-68154501
https://www.bbc.com/news/uk-england-london-68162098
https://www.bbc.com/news/uk-england-london-68137927
https://www.bbc.com/news/uk-england-london-68138737
https://www.bbc.com/news/uk-scotland-68152037
https://www.bbc.com/news/uk-england-northamptonshire-68155006
https://www.bbc.com/news/uk-england-bristol-68141749
https://www.bbc.com/news/uk-england-l

<Response [200]>
----------------------------------------------------------------------------------------------------
date:2/1/2024 start:20 total:1475
https://www.bbc.com/news/uk-68166050
https://www.bbc.com/news/business-68163180
https://www.bbc.com/news/world-europe-68173000
https://www.bbc.com/news/av/world-us-canada-68173142
https://www.bbc.com/news/world-asia-india-68151023
https://www.bbc.com/news/world-europe-68171911
https://www.bbc.com/news/world-us-canada-68171107
https://www.bbc.com/news/world-us-canada-68169406
https://www.bbc.com/news/world-middle-east-68162927
https://www.bbc.com/news/business-68005481
<Response [200]>
----------------------------------------------------------------------------------------------------
date:2/1/2024 start:30 total:1483
https://www.bbc.com/news/business-68005481
https://www.bbc.com/news/world-middle-east-68162927
https://www.bbc.com/news/entertainment-arts-68160058
https://www.bbc.com/news/av/world-us-canada-68176255
https://www.bbc.com/ne

<Response [200]>
----------------------------------------------------------------------------------------------------
date:2/1/2024 start:190 total:1582
https://www.bbc.com/news/uk-england-merseyside-68169320
https://www.bbc.com/news/uk-england-sussex-68165612
https://www.bbc.com/news/av/world-europe-68151728
https://www.bbc.com/news/uk-england-nottinghamshire-68168550
https://www.bbc.com/news/uk-england-berkshire-68169765
https://www.bbc.com/news/uk-england-devon-68164413
<Response [200]>
----------------------------------------------------------------------------------------------------
date:2/1/2024 start:200 total:1592
https://www.bbc.com/news/uk-england-cumbria-68168357
https://www.bbc.com/news/uk-england-68169282
https://www.bbc.com/news/uk-england-bristol-68164255
https://www.bbc.com/news/uk-england-somerset-68168692
https://www.bbc.com/news/uk-england-sussex-68173382
https://www.bbc.com/news/uk-england-wiltshire-68159739
https://www.bbc.com/news/england/bradford?page=1
https://

<Response [200]>
----------------------------------------------------------------------------------------------------
date:2/2/2024 start:40 total:1703
https://www.bbc.com/news/uk-68182921
https://www.bbc.com/news/av/uk-68178352
https://www.bbc.com/news/uk-68179839
https://www.bbc.com/news/entertainment-arts-68179439
https://www.bbc.com/news/science-environment-68170278
https://www.bbc.com/news/world-us-canada-68185611
https://www.bbc.com/news/world-africa-68177661
https://www.bbc.com/news/uk-68167793
https://www.bbc.com/news/uk-england-manchester-68147985
https://www.bbc.com/news/business-68183422
<Response [200]>
----------------------------------------------------------------------------------------------------
date:2/2/2024 start:50 total:1710
https://www.bbc.com/news/world-us-canada-68186945
https://www.bbc.com/news/business-68183421
https://www.bbc.com/news/world-africa-68184076
https://www.bbc.com/news/uk-england-nottinghamshire-68184043
https://www.bbc.com/news/world-us-canada-

SSLError: HTTPSConnectionPool(host='www.google.com', port=443): Max retries exceeded with url: /search?q=news+site:bbc.com/news&tbs=cdr:1,cd_min:2/2/2024,cd_max:2/2/2024&tbm=nws&start=120 (Caused by SSLError(SSLEOFError(8, 'EOF occurred in violation of protocol (_ssl.c:1007)')))

In [13]:
url_list = set(url_list)
len(url_list)

1756

In [16]:
def extract_content_from_url(url):
    headers = {
    'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/98.0.4758.102 Safari/537.36'
    }
    
    try:
        response = requests.get(url, headers=headers)
        response.raise_for_status()
    except requests.HTTPError as http_err:
        return f"HTTP error occurred: {http_err}"
    except Exception as err:
        return f"An error occurred: {err}"

    soup = BeautifulSoup(response.text, 'lxml')
    
    main_content = soup.find('main')
    content_list = []

    if main_content:
        
        pattern = re.compile(r'(text-block|subheadline-block)')

        content_divs = main_content.find_all('div', attrs={'data-component': pattern})

        for div in content_divs:
            content = ' '.join(div.stripped_strings)
            content_list.append(content)
    
    joined_string = '\n'.join(content_list)

    return joined_string


In [17]:
def fetch_url(url):
    extracted_contents = extract_content_from_url(url)
    if len(extracted_contents) > 100:
        return extracted_contents
    else:
        return None

all_news = []

with ThreadPoolExecutor(max_workers=10) as executor:
    
    future_to_url = {executor.submit(fetch_url, url): url for url in url_list}
    
    for future in tqdm(as_completed(future_to_url), total=len(url_list)):
        url = future_to_url[future]
        try:
            content = future.result()
            if content:
                print('-' * 100)
                print(content)
                all_news.append(content)
            else:
                print('-' * 100)
                print('length < 100')
        except Exception as exc:
            print(f'{url} generated an exception: {exc}')
            

  0%|          | 0/1756 [00:00<?, ?it/s]

----------------------------------------------------------------------------------------------------
A man has been charged with the murder of a 22-year-old woman who was stabbed to death.
Claudia Kambanza died after she was attacked in Hinderwell Street in Hull on Friday, Humberside Police said.
Mateus Johannes, 28, has been charged with murder and being in possession of a bladed article in a public place.
Mr Johannes, of no fixed abode, has been remanded in custody and will appear at Hull Magistrates' Court on Monday.
Follow BBC East Yorkshire and Lincolnshire on Facebook , X (formerly Twitter) , and Instagram . Send your story ideas to yorkslincs.news@bbc.co.uk
----------------------------------------------------------------------------------------------------
A 72-year-old man who had a heart attack has said an NHS rehab class has been "absolutely central" to his recovery.
Barry Lilley, from Weston Favell in Northampton, attended the sessions run by Northampton General Hospital (NG

----------------------------------------------------------------------------------------------------
length < 100
----------------------------------------------------------------------------------------------------
Tributes have been paid to a man who was killed in a car crash in Nottinghamshire.
Nathan Naughton, 26, died when a Ford Ranger crashed in Bawtry Road, Harworth, at about 02:15 GMT on Sunday.
Nottinghamshire Police said a 22-year-old woman, who has not been named, was also killed in the single-vehicle crash.
Mr Naughton, from Doncaster, South Yorkshire, has been described as "a loving son and brother".
In a statement, released by police, his father said: "He was a hard-working, outgoing lad, who was well liked and very popular.
"We are all devastated by what has happened and we miss Nathan deeply as we try to come to terms with his loss."
Police said an investigation into the cause of the crash was under way and appealed for anyone with information to contact them.
Follow BB

----------------------------------------------------------------------------------------------------
The wife of a terminally ill man has said he was discharged from a Belfast hospital without a care package in place.
Ray Bass, 67, has been told he has just a few weeks to live.
He was treated at the Royal Victoria Hospital, in the Belfast Trust area, but lives in the Western Health Trust area.
The Belfast Trust said it does not have control over how long it takes to secure care outside their area.
The Western Trust, which covers Ballinamallard, County Fermanagh, where Mr Bass lives, apologised for any distress caused.
A care package has now been put in place but Mr Bass' wife Shelley told BBC News NI that she expected one to be ready after he returned home from hospital on Monday.
"I'm reeling. I'm losing the man that I love and now I'm having to sort all these things out as well," said Mrs Bass.
"I shouldn't need to have to nurse my husband when I'm trying to get over the fact that I'

----------------------------------------------------------------------------------------------------
The residents of a seaside town are coming together to look at how they can tackle climate change. Bude, on the north Cornwall coast, has been described as the UK's Maldives - idyllic and beautiful but facing an imminent threat due to rising sea levels.
As Alara Vural Wedgwood prepares to head out to train with the local Surf Life Saving Club, she says the beach and seafront are what brings the community together.
"People live here, it's not just a tourist place," the marketing consultant says.
"There's such a strong sense of community and a lot of that is based around the seafront. It's what brings the community of Bude together."
But Mrs Vural Wedgwood fears "with climate change, there might not be a seafront in the way that we know it".
Images created by the Environment Agency show the potential impact rising sea levels could have on Bude.
The visualisations for Crooklets Beach show 

...

----------------------------------------------------------------------------------------------------
Class sizes at a high school are sometimes reaching 90 pupils due to teacher shortages, staff claim.
Unions are consulting members about strike action over issues at Longsands Academy in St Neots , Cambridgeshire.
A staff member, who asked not to be named, said: "Teachers are leaving in droves."
Principal Dr Catherine Cusick said the school was meeting with unions to discuss their concerns and was working hard to improve.
A staff member told the BBC on at least two occasions so far this term, groups of between 60 and 90 students had been supervised by staff in the main hall while they worked from text books.
'Culture of fear'
"Teachers are leaving in their droves due to unacceptable management practices including prescribed teaching methods, strict behaviour rules, curriculum changes, workload, constantly being watched and targeted, poor communication, diminished staff student relations

----------------------------------------------------------------------------------------------------
length < 100
----------------------------------------------------------------------------------------------------
Lord Sugar has said wannabe influencers are weeded out during the selection process for The Apprentice, as his team can "smell them a mile off".
The Apprentice returns to screens this week with 18 new candidates competing for a Â£250,000 business investment.
Lord Sugar said his own staff sit in on casting calls and help avoid candidates who are only hungry for fame.
But he acknowledged the show needs "a whole array of characters" in order to be entertaining for viewers.
Lord Sugar told BBC culture correspondent Charlotte Gallagher it was a concern that some people apply for the show hoping only for a profile boost.
"That's why the production company that's been making this thing for 18 years, and my staff who go along to the auditions, can smell them a mile off," he said.
"A

----------------------------------------------------------------------------------------------------
No serving leader in the European Union has led their country for as long as Viktor Orban.
Since 2010, he has transformed Hungary into what the European Parliament has denounced as a "hybrid regime of electoral autocracy". He appears uncertain how to describe his own invention, trying both "illiberal democracy" and "Christian liberty".
Either way, he has learned to maintain and constantly strengthen his grip on power.
He has repeatedly clashed with European Union colleagues on migration and the war in Ukraine, and has prevented â¬50bn (Â£43bn; $55bn) of EU funds being handed to Kyiv to help Ukraine survive.
Hungary also finds itself the only Nato member country not to have approved Swedish membership, even though its prime minister claims to be in favour.
Andras Kosa entitled his biography of Viktor Orban, Man of Chaos, suggesting he has a way of presenting himself as the only solution

----------------------------------------------------------------------------------------------------
A school has received a share of the Â£93m government fund given to more than 1,000 grassroots sports projects in the country.
In Hertfordshire one of the largest grants went Kings Langley School which each got Â£708,117 for a new pitch.
Head teacher David Fisher said he was "delighted to be enhancing the facilities at the school".
Sports Minister Stuart Andrew said the funding aids his priority of getting more people active by 2030.
About 50 projects in Bedfordshire, Hertfordshire and Buckinghamshire will get a share of the funding.
Stratton Upper School, Biggleswade, and Katherine Warrington School, Harpenden, will get Â£700,000 for new artificial pitches while Ousedale School in Olney, Milton Keynes, will get Â£649,619 for a new pitch.
Maple Cross JMI School and Nursery School in the Hertfordshire town of Rickmansworth will get money for new goalposts.
Mr Fisher said work on his scho

----------------------------------------------------------------------------------------------------
Consultants have rejected the latest pay offer from the government in England - by the narrowest of margins.
The British Medical Association urged ministers to better the deal, after 51% voted against it, with a 65% turnout.
The deal offered was worth an extra 4.95%, on average, in basic pay from this month - and would have come on top of the 6% rise granted in April.
Health Secretary Victoria Atkins said she was disappointed the "fair and reasonable" offer had been rejected.
"The government is carefully considering the next steps," she added.
Consultants staged four walkouts last year. They have a strike mandate until June but have yet to announce further action.
Those at the much smaller Hospital Consultants and Specialists Union also rejected the deal.
The amount individual doctors would have received, on top of the 6% rise already granted, would have varied from 0% to nearly 13%, as

In [20]:
all_news_cut = [x[:5000] for x in all_news]
all_news_cut = all_news_cut[-1000:]
len(all_news_cut), max([len(x) for x in all_news_cut])

(1000, 5000)

In [21]:
import json

path = 'bbc_news_240125_to_240203.json'

with open(path, 'w') as f:
    json.dump(all_news_cut, f, ensure_ascii=True, indent=4)

In [23]:
with open(path, 'r') as f:
    check = json.load(f)
check

['Canada has announced plans to again delay an expansion to its medical assistance in dying (maid) programme for people who have a mental illness.\nIt comes after a parliamentary committee recommended a pause on the expansion, which was originally set to come into effect on 17 March.\nOttawa had also been warned by the provinces that they had not had time to properly prepare.\nLegislation was tabled on Thursday to delay the expansion to 2027.\nThe government "has heard - and agrees - that the health system is not yet ready for this expansion", Health Canada said in a statement.\nConcerns have been raised by provinces across the country, which oversee healthcare services, about whether the system is ready and robust enough to handle the expansion.\nSpeaking on Thursday in Ottawa, federal Health Minister Mark Holland said the government accepts the equivalency of mental suffering and physical suffering, but that it is a "question of readiness".\nHe said his provincial counterparts, as we